In [6]:
!pip install pycaret
!pip install catboost|
!pip install xgboost
from pycaret.utils import enable_colab
enable_colab()

/bin/bash: -c: line 1: syntax error: unexpected end of file
Colab mode enabled.


In [7]:
import pandas as pd
import numpy as np
import os
import pycaret

from tqdm import tqdm

In [8]:
data = pd.read_csv('2013-2018년_가스공급량_기온_습도_기압01.csv')
data

year  month  day  weekday  시간  구분       공급량   기온    습도      기압
0       2013      1    1        1   1   0  2497.129 -8.5  57.0  1010.0
1       2013      1    1        1   1   1  2169.093 -8.5  57.0  1010.0
2       2013      1    1        1   1   2   226.178 -8.5  57.0  1010.0
3       2013      1    1        1   1   3  1434.516 -8.5  57.0  1010.0
4       2013      1    1        1   1   4  3272.837 -8.5  57.0  1010.0
...      ...    ...  ...      ...  ..  ..       ...  ...   ...     ...
368083  2018     12   31        0  24   2   237.911 -5.5  54.0  1024.1
368084  2018     12   31        0  24   3  1422.478 -5.5  54.0  1024.1
368085  2018     12   31        0  24   4  3534.260 -5.5  54.0  1024.1
368086  2018     12   31        0  24   5  3982.757 -5.5  54.0  1024.1
368087  2018     12   31        0  24   6   560.896 -5.5  54.0  1024.1

[368088 rows x 10 columns]

In [9]:
sub = pd.read_csv('sample_submission.csv')
sub

일자|시간|구분  공급량
0      2019-01-01 01 A    0
1      2019-01-01 02 A    0
2      2019-01-01 03 A    0
3      2019-01-01 04 A    0
4      2019-01-01 05 A    0
...                ...  ...
15115  2019-03-31 20 H    0
15116  2019-03-31 21 H    0
15117  2019-03-31 22 H    0
15118  2019-03-31 23 H    0
15119  2019-03-31 24 H    0

[15120 rows x 2 columns]

In [10]:
sub['일자'] = sub['일자|시간|구분'].str.split().str[0]
sub['시간'] = sub['일자|시간|구분'].str.split().str[1]
sub['구분'] = sub['일자|시간|구분'].str.split().str[2]
d_map = {}
for i, d in enumerate(sub['구분'].unique()):
    d_map[d] = i
sub['구분'] = sub['구분'].map(d_map)
sub['일자'] = pd.to_datetime(sub['일자'])
sub['month'] = sub['일자'].dt.month
sub['day'] = sub['일자'].dt.day
sub['weekday'] = sub['일자'].dt.weekday

In [11]:
sub

일자|시간|구분  공급량         일자  시간  구분  month  day  weekday
0      2019-01-01 01 A    0 2019-01-01  01   0      1    1        1
1      2019-01-01 02 A    0 2019-01-01  02   0      1    1        1
2      2019-01-01 03 A    0 2019-01-01  03   0      1    1        1
3      2019-01-01 04 A    0 2019-01-01  04   0      1    1        1
4      2019-01-01 05 A    0 2019-01-01  05   0      1    1        1
...                ...  ...        ...  ..  ..    ...  ...      ...
15115  2019-03-31 20 H    0 2019-03-31  20   6      3   31        6
15116  2019-03-31 21 H    0 2019-03-31  21   6      3   31        6
15117  2019-03-31 22 H    0 2019-03-31  22   6      3   31        6
15118  2019-03-31 23 H    0 2019-03-31  23   6      3   31        6
15119  2019-03-31 24 H    0 2019-03-31  24   6      3   31        6

[15120 rows x 8 columns]

In [12]:
data_cal = data[['공급량', '기온','습도','기압']]
data_cal.columns = ['공급량_cal', '기온_cal','습도_cal','기압_cal']
data_cal = data_cal.shift(periods=7, axis=0, fill_value = 0)
data_cal['공급량_cal'][0:7] = data['공급량'][0:7]
data_cal['기온_cal'][0:7] = data['기온'][0:7]
data_cal['습도_cal'][0:7] = data['습도'][0:7]
data_cal['기압_cal'][0:7] = data['기압'][0:7]
data_cal.head(10)

공급량_cal  기온_cal  습도_cal  기압_cal
0  2497.129    -8.5    57.0  1010.0
1  2169.093    -8.5    57.0  1010.0
2   226.178    -8.5    57.0  1010.0
3  1434.516    -8.5    57.0  1010.0
4  3272.837    -8.5    57.0  1010.0
5  3560.365    -8.5    57.0  1010.0
6   562.964    -8.5    57.0  1010.0
7  2497.129    -8.5    57.0  1010.0
8  2169.093    -8.5    57.0  1010.0
9   226.178    -8.5    57.0  1010.0

In [13]:
column_list = ['공급량_r', '기온_r', '습도_r', '기압_r']
for col in column_list:
    data[col] = pd.Series()
data = data.fillna(0)
data

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  This is separate from the ipykernel package so we can avoid doing imports until


year  month  day  weekday  시간  ...      기압  공급량_r  기온_r  습도_r  기압_r
0       2013      1    1        1   1  ...  1010.0    0.0   0.0   0.0   0.0
1       2013      1    1        1   1  ...  1010.0    0.0   0.0   0.0   0.0
2       2013      1    1        1   1  ...  1010.0    0.0   0.0   0.0   0.0
3       2013      1    1        1   1  ...  1010.0    0.0   0.0   0.0   0.0
4       2013      1    1        1   1  ...  1010.0    0.0   0.0   0.0   0.0
...      ...    ...  ...      ...  ..  ...     ...    ...   ...   ...   ...
368083  2018     12   31        0  24  ...  1024.1    0.0   0.0   0.0   0.0
368084  2018     12   31        0  24  ...  1024.1    0.0   0.0   0.0   0.0
368085  2018     12   31        0  24  ...  1024.1    0.0   0.0   0.0   0.0
368086  2018     12   31        0  24  ...  1024.1    0.0   0.0   0.0   0.0
368087  2018     12   31        0  24  ...  1024.1    0.0   0.0   0.0   0.0

[368088 rows x 14 columns]

In [14]:
data['공급량_r'] = (data['공급량'] - data_cal['공급량_cal']) / data_cal['공급량_cal']
data['기압_r'] = (data['기압'] - data_cal['기압_cal']) / data_cal['기압_cal']
data['기온_r'] = (data['기온'] - data_cal['기온_cal']) / data_cal['기온_cal']
data['습도_r'] = (data['습도'] - data_cal['습도_cal']) / data_cal['습도_cal']


In [15]:
data.head(20)

year  month  day  weekday  ...     공급량_r      기온_r      습도_r      기압_r
0   2013      1    1        1  ...  0.000000 -0.000000  0.000000  0.000000
1   2013      1    1        1  ...  0.000000 -0.000000  0.000000  0.000000
2   2013      1    1        1  ...  0.000000 -0.000000  0.000000  0.000000
3   2013      1    1        1  ...  0.000000 -0.000000  0.000000  0.000000
4   2013      1    1        1  ...  0.000000 -0.000000  0.000000  0.000000
5   2013      1    1        1  ...  0.000000 -0.000000  0.000000  0.000000
6   2013      1    1        1  ...  0.000000 -0.000000  0.000000  0.000000
7   2013      1    1        1  ... -0.053607 -0.011765  0.052632 -0.000594
8   2013      1    1        1  ... -0.054106 -0.011765  0.052632 -0.000594
9   2013      1    1        1  ... -0.045981 -0.011765  0.052632 -0.000594
10  2013      1    1        1  ... -0.061958 -0.011765  0.052632 -0.000594
11  2013      1    1        1  ... -0.065910 -0.011765  0.052632 -0.000594
12  2013      1    1        1  ... -0.057893 -0.011765  0.052632 -0.000594
13  2013      1    1        1  ... -0.056373 -0.011765  0.052632 -0.000594
14  2013      1    1        1  ... -0.044329 -0.035714 -0.033333 -0.000198
15  2013      1    1        1  ... -0.062620 -0.035714 -0.033333 -0.000198
16  2013      1    1        1  ... -0.063028 -0.035714 -0.033333 -0.000198
17  2013      1    1        1  ... -0.055647 -0.035714 -0.033333 -0.000198
18  2013      1    1        1  ... -0.048856 -0.035714 -0.033333 -0.000198
19  2013      1    1        1  ... -0.071100 -0.035714 -0.033333 -0.000198

[20 rows x 14 columns]

In [16]:
data.corr()

year         month  ...          습도_r          기압_r
year     1.000000e+00 -1.753370e-04  ...  1.320719e-03  3.669361e-04
month   -1.753370e-04  1.000000e+00  ... -9.138293e-03  7.103206e-03
day      2.016196e-04  1.097865e-02  ...  8.074998e-04 -2.753887e-03
weekday  6.682591e-04  8.603019e-04  ...  1.629616e-03 -7.188976e-03
시간       5.226277e-20 -1.617354e-20  ...  1.868013e-01  1.056632e-01
구분       0.000000e+00  0.000000e+00  ... -3.370443e-19 -2.052217e-20
공급량      1.175500e-02 -1.547875e-01  ... -2.206102e-02  4.219052e-02
기온       5.021687e-03  2.292884e-01  ... -1.136764e-02 -1.137418e-01
습도      -7.080051e-02  1.439818e-01  ...  8.704338e-02  1.392286e-01
기압       3.361455e-02 -3.481464e-02  ... -1.854994e-02  2.939562e-02
공급량_r   -2.879963e-03  6.453832e-03  ...  2.734817e-03  1.018615e-01
기온_r     2.055320e-03 -1.850758e-03  ... -5.397901e-02 -2.460777e-02
습도_r     1.320719e-03 -9.138293e-03  ...  1.000000e+00  1.309223e-01
기압_r     3.669361e-04  7.103206e-03  ...  1.309223e-01  1.000000e+00

[14 rows x 14 columns]

In [16]:
data_features = data[['month', 'weekday', '시간', '기온_r', '습도_r', '기압_r', '공급량_r']]
data_features

month  weekday  시간      기온_r      습도_r      기압_r     공급량_r
0           1        1   1 -0.000000  0.000000  0.000000  0.000000
1           1        1   1 -0.000000  0.000000  0.000000  0.000000
2           1        1   1 -0.000000  0.000000  0.000000  0.000000
3           1        1   1 -0.000000  0.000000  0.000000  0.000000
4           1        1   1 -0.000000  0.000000  0.000000  0.000000
...       ...      ...  ..       ...       ...       ...       ...
368083     12        0  24  0.057692  0.148936 -0.000488 -0.032961
368084     12        0  24  0.057692  0.148936 -0.000488 -0.124164
368085     12        0  24  0.057692  0.148936 -0.000488 -0.056485
368086     12        0  24  0.057692  0.148936 -0.000488 -0.052736
368087     12        0  24  0.057692  0.148936 -0.000488 -0.081933

[368088 rows x 7 columns]

In [17]:
from pycaret.regression import *

In [13]:
data_temp = data[['month', 'weekday', '시간', '기온', '구분']]
data_temp = data_temp.loc[data_temp['구분'] == 0]
data_temp = data_temp.reset_index(drop=True)
data_temp = data_temp[['month', 'weekday', '시간', '기온']]
data_temp

month  weekday  시간   기온
0          1        1   1 -8.5
1          1        1   2 -8.4
2          1        1   3 -8.1
3          1        1   4 -8.2
4          1        1   5 -8.2
...      ...      ...  ..  ...
52579     12        0  20 -3.7
52580     12        0  21 -4.6
52581     12        0  22 -5.4
52582     12        0  23 -5.2
52583     12        0  24 -5.5

[52584 rows x 4 columns]

In [14]:
temp_setup = setup(data=data_temp,  numeric_features = ['month', 'weekday'], target='기온')

Description             Value
0                               session_id              3871
1                                   Target                기온
2                            Original Data        (52584, 4)
3                           Missing Values             False
4                         Numeric Features                 3
5                     Categorical Features                 0
6                         Ordinal Features             False
7                High Cardinality Features             False
8                  High Cardinality Method              None
9                    Transformed Train Set        (36808, 3)
10                    Transformed Test Set        (15776, 3)
11                      Shuffle Train-Test              True
12                     Stratify Train-Test             False
13                          Fold Generator             KFold
14                             Fold Number                10
15                                CPU Jobs                -1
16                                 Use GPU             False
17                          Log Experiment             False
18                         Experiment Name  reg-default-name
19                                     USI              dbb6
20                         Imputation Type            simple
21          Iterative Imputation Iteration              None
22                         Numeric Imputer              mean
23      Iterative Imputation Numeric Model              None
24                     Categorical Imputer          constant
25  Iterative Imputation Categorical Model              None
26           Unknown Categoricals Handling    least_frequent
27                               Normalize             False
28                        Normalize Method              None
29                          Transformation             False
30                   Transformation Method              None
31                                     PCA             False
32                              PCA Method              None
33                          PCA Components              None
34                     Ignore Low Variance             False
35                     Combine Rare Levels             False
36                    Rare Level Threshold              None
37                         Numeric Binning             False
38                         Remove Outliers             False
39                      Outliers Threshold              None
40                Remove Multicollinearity             False
41             Multicollinearity Threshold              None
42             Remove Perfect Collinearity              True
43                              Clustering             False
44                    Clustering Iteration              None
45                     Polynomial Features             False
46                       Polynomial Degree              None
47                    Trignometry Features             False
48                    Polynomial Threshold              None
49                          Group Features             False
50                       Feature Selection             False
51                Feature Selection Method           classic
52            Features Selection Threshold              None
53                     Feature Interaction             False
54                           Feature Ratio             False
55                   Interaction Threshold              None
56                        Transform Target             False
57                 Transform Target Method           box-cox

In [ ]:
model_temp = compare_models(sort='MAPE')

IntProgress(value=0, description='Processing: ', max=99)

Initiated  . . . . . . . . . . . . . . . . . .                     02:27:09
Status     . . . . . . . . . . . . . . . . . .             Fitting 10 Folds
Estimator  . . . . . . . . . . . . . . . . . .  Gradient Boosting Regressor

Model      MAE       MSE     RMSE      R2  \
dt          Decision Tree Regressor   3.1405   16.4333   4.0534  0.8706   
et            Extra Trees Regressor   3.1405   16.4332   4.0534  0.8706   
rf          Random Forest Regressor   3.1417   16.4471   4.0550  0.8705   
knn           K Neighbors Regressor   3.3290   18.4472   4.2946  0.8547   
lr                Linear Regression   9.3391  119.0899  10.9127  0.0624   
ridge              Ridge Regression   9.3391  119.0899  10.9127  0.0624   
lar          Least Angle Regression   9.3391  119.0899  10.9127  0.0624   
br                   Bayesian Ridge   9.3394  119.0899  10.9127  0.0624   
omp     Orthogonal Matching Pursuit   9.3818  120.5481  10.9792  0.0509   
en                      Elastic Net   9.3600  119.1484  10.9153  0.0619   
lasso              Lasso Regression   9.3648  119.1878  10.9172  0.0616   
huber               Huber Regressor   9.2481  120.6199  10.9824  0.0503   
llar   Lasso Least Angle Regression   9.7259  127.0676  11.2723 -0.0004   
par    Passive Aggressive Regressor  13.2735  288.2810  16.2560 -1.2726   

        RMSLE    MAPE  TT (Sec)  
dt     0.5365  0.8222     0.040  
et     0.5365  0.8222     1.494  
rf     0.5363  0.8229     1.943  
knn    0.5522  0.8915     0.089  
lr     0.8510  2.9911     0.327  
ridge  0.8510  2.9911     0.018  
lar    0.8510  2.9911     0.018  
br     0.8510  2.9914     0.020  
omp    0.8531  3.0042     0.019  
en     0.8534  3.0052     0.021  
lasso  0.8538  3.0084     0.019  
huber  0.8557  3.1041     0.099  
llar   0.8833  3.1574     0.019  
par    1.1168  3.7277     0.037

In [ ]:
finalized = finalize_model(model_temp)
prediction = predict_model(finalized, data=sub)
prediction

In [ ]:
sub['기온'] = prediction.Label

In [ ]:
data_temp = data[['month', 'weekday', '시간', '습도', '구분']]
data_temp = data_temp.loc[data_temp['구분'] == 0]
data_temp = data_temp.reset_index(drop=True)
data_temp = data_temp[['month', 'weekday', '시간', '습도']]
data_temp

In [ ]:
temp_setup = setup(data=data_temp, numeric_features = ['month', 'weekday'], target='습도', silent=True)

In [ ]:
model_temp = compare_models(sort='MAPE')

In [ ]:
finalized = finalize_model(model_temp)
prediction = predict_model(finalized, data=sub)
sub['습도'] = prediction.Label
sub

In [ ]:
data_temp = data[['month', 'weekday', '시간', '기압', '구분']]
data_temp = data_temp.loc[data_temp['구분'] == 0]
data_temp = data_temp.reset_index(drop=True)
data_temp = data_temp[['month', 'weekday', '시간', '기압']]
data_temp

In [ ]:
temp_setup = setup(data=data_temp, numeric_features = ['month', 'weekday'], target='기압', silent=True)

In [ ]:
model_temp = compare_models(sort='MAPE')

In [ ]:
finalized = finalize_model(model_temp)
prediction = predict_model(finalized, data=sub)
sub['기압'] = prediction.Label
sub

In [ ]:
sub.isna().sum()

In [ ]:
sub_cal = sub[['공급량', '기온','습도','기압']]
sub_cal.columns = ['공급량_cal', '기온_cal','습도_cal','기압_cal']
sub_cal = sub_cal.shift(periods=7, axis=0, fill_value = 0)
sub_cal['공급량_cal'][0:7] = sub['공급량'][0:7]
sub_cal['기온_cal'][0:7] = sub['기온'][0:7]
sub_cal['습도_cal'][0:7] = sub['습도'][0:7]
sub_cal['기압_cal'][0:7] = sub['기압'][0:7]
sub_cal.head(10)

In [ ]:
column_list = ['공급량_r', '기온_r', '습도_r', '기압_r']
for col in column_list:
    sub[col] = pd.Series()
sub = sub.fillna(0)
sub

In [ ]:
#sub['공급량_r'] = (sub['공급량'] - sub_cal['공급량_cal']) / sub_cal['공급량_cal']
sub['기압_r'] = (sub['기압'] - sub_cal['기압_cal']) / sub_cal['기압_cal']
sub['기온_r'] = (sub['기온'] - sub_cal['기온_cal']) / sub_cal['기온_cal']
sub['습도_r'] = (sub['습도'] - sub_cal['습도_cal']) / sub_cal['습도_cal']
sub

In [18]:
sub = pd.read_csv('sub_with_stationary.csv')
sub

일자|시간|구분  공급량          일자  시간  구분  month  day  weekday  \
0      2019-01-01 01 A    0  2019-01-01   1   0      1    1        1   
1      2019-01-01 02 A    0  2019-01-01   2   0      1    1        1   
2      2019-01-01 03 A    0  2019-01-01   3   0      1    1        1   
3      2019-01-01 04 A    0  2019-01-01   4   0      1    1        1   
4      2019-01-01 05 A    0  2019-01-01   5   0      1    1        1   
...                ...  ...         ...  ..  ..    ...  ...      ...   
15115  2019-03-31 20 H    0  2019-03-31  20   6      3   31        6   
15116  2019-03-31 21 H    0  2019-03-31  21   6      3   31        6   
15117  2019-03-31 22 H    0  2019-03-31  22   6      3   31        6   
15118  2019-03-31 23 H    0  2019-03-31  23   6      3   31        6   
15119  2019-03-31 24 H    0  2019-03-31  24   6      3   31        6   

             기온         습도           기압  공급량_r      기온_r      습도_r      기압_r  
0     -3.932410  60.474356  1014.608995    0.0 -0.000000  0.000000  0.000000  
1     -4.281533  61.425472  1014.608995    0.0 -0.000000  0.000000  0.000000  
2     -4.570999  61.870234  1014.583028    0.0 -0.000000  0.000000  0.000000  
3     -4.876857  62.783809  1014.555879    0.0 -0.000000  0.000000  0.000000  
4     -5.053840  63.241103  1014.555879    0.0 -0.000000  0.000000  0.000000  
...         ...        ...          ...    ...       ...       ...       ...  
15115  7.421519  52.899716  1009.006903    0.0 -0.326889  0.462267 -0.000626  
15116  6.743935  56.268820  1009.442362    0.0 -0.418886  0.627406  0.000832  
15117  6.199907  58.926853  1009.642280    0.0 -0.474202  0.703771  0.001394  
15118  5.691406  60.800954  1009.687945    0.0 -0.512884  0.731248  0.001449  
15119  5.320811  61.497685  1009.687945    0.0 -0.513671  0.592089  0.001449  

[15120 rows x 15 columns]

In [19]:
data_features = data[['month', 'weekday', '구분', '시간', '기온_r', '습도_r', '기압_r', '공급량_r']]
data_features

month  weekday  구분  시간      기온_r      습도_r      기압_r     공급량_r
0           1        1   0   1 -0.000000  0.000000  0.000000  0.000000
1           1        1   1   1 -0.000000  0.000000  0.000000  0.000000
2           1        1   2   1 -0.000000  0.000000  0.000000  0.000000
3           1        1   3   1 -0.000000  0.000000  0.000000  0.000000
4           1        1   4   1 -0.000000  0.000000  0.000000  0.000000
...       ...      ...  ..  ..       ...       ...       ...       ...
368083     12        0   2  24  0.057692  0.148936 -0.000488 -0.032961
368084     12        0   3  24  0.057692  0.148936 -0.000488 -0.124164
368085     12        0   4  24  0.057692  0.148936 -0.000488 -0.056485
368086     12        0   5  24  0.057692  0.148936 -0.000488 -0.052736
368087     12        0   6  24  0.057692  0.148936 -0.000488 -0.081933

[368088 rows x 8 columns]

In [20]:
data_features_a = data_features[data_features['구분'] == 0].reset_index(drop=True)
data_features_b = data_features[data_features['구분'] == 1].reset_index(drop=True)
data_features_c = data_features[data_features['구분'] == 2].reset_index(drop=True)
data_features_d = data_features[data_features['구분'] == 3].reset_index(drop=True)
data_features_e = data_features[data_features['구분'] == 4].reset_index(drop=True)
data_features_f = data_features[data_features['구분'] == 5].reset_index(drop=True)
data_features_g = data_features[data_features['구분'] == 6].reset_index(drop=True)

In [21]:
sub_a = sub[sub['구분'] == 0].drop(columns=['공급량_r']).reset_index(drop=True)
sub_b = sub[sub['구분'] == 1].drop(columns=['공급량_r']).reset_index(drop=True)
sub_c = sub[sub['구분'] == 2].drop(columns=['공급량_r']).reset_index(drop=True)
sub_d = sub[sub['구분'] == 3].drop(columns=['공급량_r']).reset_index(drop=True)
sub_e = sub[sub['구분'] == 4].drop(columns=['공급량_r']).reset_index(drop=True)
sub_f = sub[sub['구분'] == 5].drop(columns=['공급량_r']).reset_index(drop=True)
sub_g = sub[sub['구분'] == 6].drop(columns=['공급량_r']).reset_index(drop=True)

In [22]:
data_features_f

month  weekday  구분  시간      기온_r      습도_r      기압_r     공급량_r
0          1        1   5   1 -0.000000  0.000000  0.000000  0.000000
1          1        1   5   2 -0.011765  0.052632 -0.000594 -0.057893
2          1        1   5   3 -0.035714 -0.033333 -0.000198 -0.071100
3          1        1   5   4  0.012346  0.000000 -0.000991 -0.026164
4          1        1   5   5 -0.000000  0.051724 -0.000893  0.005350
...      ...      ...  ..  ..       ...       ...       ...       ...
52579     12        0   5  20  0.193548 -0.093023 -0.000585  0.000740
52580     12        0   5  21  0.243243  0.128205 -0.000098 -0.036654
52581     12        0   5  22  0.173913  0.045455 -0.000390 -0.029404
52582     12        0   5  23 -0.037037  0.021739  0.000195 -0.034543
52583     12        0   5  24  0.057692  0.148936 -0.000488 -0.052736

[52584 rows x 8 columns]

In [23]:
sub_a

일자|시간|구분  공급량          일자  시간  구분  month  day  weekday        기온  \
0     2019-01-01 01 A    0  2019-01-01   1   0      1    1        1 -3.932410   
1     2019-01-01 02 A    0  2019-01-01   2   0      1    1        1 -4.281533   
2     2019-01-01 03 A    0  2019-01-01   3   0      1    1        1 -4.570999   
3     2019-01-01 04 A    0  2019-01-01   4   0      1    1        1 -4.876857   
4     2019-01-01 05 A    0  2019-01-01   5   0      1    1        1 -5.053840   
...               ...  ...         ...  ..  ..    ...  ...      ...       ...   
2155  2019-03-31 20 A    0  2019-03-31  20   0      3   31        6  7.421519   
2156  2019-03-31 21 A    0  2019-03-31  21   0      3   31        6  6.743935   
2157  2019-03-31 22 A    0  2019-03-31  22   0      3   31        6  6.199907   
2158  2019-03-31 23 A    0  2019-03-31  23   0      3   31        6  5.691406   
2159  2019-03-31 24 A    0  2019-03-31  24   0      3   31        6  5.320811   

             습도           기압      기온_r      습도_r      기압_r  
0     60.474356  1014.608995 -0.000000  0.000000  0.000000  
1     61.425472  1014.608995 -0.000000  0.000000  0.000000  
2     61.870234  1014.583028 -0.000000  0.000000  0.000000  
3     62.783809  1014.555879 -0.000000  0.000000  0.000000  
4     63.241103  1014.555879 -0.000000  0.000000  0.000000  
...         ...          ...       ...       ...       ...  
2155  52.899716  1009.006903 -0.326889  0.462267 -0.000626  
2156  56.268820  1009.442362 -0.418886  0.627406  0.000832  
2157  58.926853  1009.642280 -0.474202  0.703771  0.001394  
2158  60.800954  1009.687945 -0.512884  0.731248  0.001449  
2159  61.497685  1009.687945 -0.513671  0.592089  0.001449  

[2160 rows x 14 columns]

In [24]:
sub_b

일자|시간|구분  공급량          일자  시간  구분  month  day  weekday        기온  \
0     2019-01-01 01 B    0  2019-01-01   1   1      1    1        1 -3.932410   
1     2019-01-01 02 B    0  2019-01-01   2   1      1    1        1 -4.281533   
2     2019-01-01 03 B    0  2019-01-01   3   1      1    1        1 -4.570999   
3     2019-01-01 04 B    0  2019-01-01   4   1      1    1        1 -4.876857   
4     2019-01-01 05 B    0  2019-01-01   5   1      1    1        1 -5.053840   
...               ...  ...         ...  ..  ..    ...  ...      ...       ...   
2155  2019-03-31 20 B    0  2019-03-31  20   1      3   31        6  7.421519   
2156  2019-03-31 21 B    0  2019-03-31  21   1      3   31        6  6.743935   
2157  2019-03-31 22 B    0  2019-03-31  22   1      3   31        6  6.199907   
2158  2019-03-31 23 B    0  2019-03-31  23   1      3   31        6  5.691406   
2159  2019-03-31 24 B    0  2019-03-31  24   1      3   31        6  5.320811   

             습도           기압      기온_r      습도_r      기압_r  
0     60.474356  1014.608995 -1.404810  0.403709  0.006300  
1     61.425472  1014.608995 -1.514648  0.256784  0.005954  
2     61.870234  1014.583028 -1.615911  0.169576  0.005526  
3     62.783809  1014.555879 -1.723147  0.115783  0.005066  
4     63.241103  1014.555879 -1.815148  0.073214  0.004867  
...         ...          ...       ...       ...       ...  
2155  52.899716  1009.006903 -0.326889  0.462267 -0.000626  
2156  56.268820  1009.442362 -0.418886  0.627406  0.000832  
2157  58.926853  1009.642280 -0.474202  0.703771  0.001394  
2158  60.800954  1009.687945 -0.512884  0.731248  0.001449  
2159  61.497685  1009.687945 -0.513671  0.592089  0.001449  

[2160 rows x 14 columns]

In [27]:
models()

Name  ...  Turbo
ID                                           ...       
lr                        Linear Regression  ...   True
lasso                      Lasso Regression  ...   True
ridge                      Ridge Regression  ...   True
en                              Elastic Net  ...   True
lar                  Least Angle Regression  ...   True
llar           Lasso Least Angle Regression  ...   True
omp             Orthogonal Matching Pursuit  ...   True
br                           Bayesian Ridge  ...   True
ard       Automatic Relevance Determination  ...  False
par            Passive Aggressive Regressor  ...   True
ransac              Random Sample Consensus  ...  False
tr                       TheilSen Regressor  ...  False
huber                       Huber Regressor  ...   True
kr                             Kernel Ridge  ...  False
svm               Support Vector Regression  ...  False
knn                   K Neighbors Regressor  ...   True
dt                  Decision Tree Regressor  ...   True
rf                  Random Forest Regressor  ...   True
et                    Extra Trees Regressor  ...   True
ada                      AdaBoost Regressor  ...   True
gbr             Gradient Boosting Regressor  ...   True
mlp                           MLP Regressor  ...  False
lightgbm    Light Gradient Boosting Machine  ...   True
catboost                 CatBoost Regressor  ...   True
dummy                       Dummy Regressor  ...   True

[25 rows x 3 columns]

In [28]:
setup_a = setup(data=data_features_a, target='공급량_r', use_gpu=True, silent=True)
model_best = create_model('lightgbm')

MAE     MSE    RMSE      R2   RMSLE    MAPE
0     0.0246  0.0013  0.0354  0.9383  0.0285  1.2422
1     0.0253  0.0012  0.0349  0.9414  0.0287  0.7899
2     0.0248  0.0013  0.0365  0.9333  0.0291  1.2997
3     0.0253  0.0013  0.0360  0.9368  0.0293  1.0738
4     0.0257  0.0015  0.0385  0.9257  0.0306  0.8718
5     0.0251  0.0013  0.0354  0.9397  0.0293  1.0249
6     0.0253  0.0013  0.0357  0.9371  0.0293  1.4918
7     0.0256  0.0014  0.0375  0.9307  0.0304  1.3055
8     0.0255  0.0013  0.0355  0.9412  0.0292  1.0417
9     0.0264  0.0113  0.1062  0.6377  0.0437  1.3782
Mean  0.0254  0.0023  0.0432  0.9062  0.0308  1.1519
SD    0.0005  0.0030  0.0210  0.0896  0.0043  0.2154

In [29]:
prediction = predict_model(model_best, data=sub_a)
sub_a['공급량_r'] = prediction.Label
sub_a

일자|시간|구분  공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 A    0  2019-01-01  ...  0.000000  0.000000 -0.112546
1     2019-01-01 02 A    0  2019-01-01  ...  0.000000  0.000000 -0.142575
2     2019-01-01 03 A    0  2019-01-01  ...  0.000000  0.000000 -0.103991
3     2019-01-01 04 A    0  2019-01-01  ...  0.000000  0.000000  0.016013
4     2019-01-01 05 A    0  2019-01-01  ...  0.000000  0.000000  0.124702
...               ...  ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 A    0  2019-03-31  ...  0.462267 -0.000626  0.047013
2156  2019-03-31 21 A    0  2019-03-31  ...  0.627406  0.000832 -0.009759
2157  2019-03-31 22 A    0  2019-03-31  ...  0.703771  0.001394 -0.029736
2158  2019-03-31 23 A    0  2019-03-31  ...  0.731248  0.001449 -0.042871
2159  2019-03-31 24 A    0  2019-03-31  ...  0.592089  0.001449 -0.051614

[2160 rows x 15 columns]

In [30]:
setup_b = setup(data=data_features_b, target='공급량_r', use_gpu=True, silent=True)
model_best = create_model('lightgbm')
prediction = predict_model(model_best, data=sub_b)
sub_b['공급량_r'] = prediction.Label
sub_b

MAE     MSE    RMSE      R2   RMSLE    MAPE
0     0.0346  0.0152  0.1235  0.6846  0.0515  1.3112
1     0.0341  0.0035  0.0592  0.9082  0.0436  1.5238
2     0.0346  0.0100  0.1002  0.7637  0.0479  0.8909
3     0.0334  0.0031  0.0554  0.9156  0.0418  5.4483
4     0.0324  0.0025  0.0498  0.9299  0.0379  1.5036
5     0.0326  0.0046  0.0676  0.8746  0.0430  1.4490
6     0.0322  0.0026  0.0514  0.9244  0.0396  1.1748
7     0.0330  0.0027  0.0518  0.9235  0.0398  1.1385
8     0.0323  0.0029  0.0538  0.9185  0.0395  1.3960
9     0.0332  0.0125  0.1119  0.7099  0.0504  1.1667
Mean  0.0332  0.0060  0.0725  0.8553  0.0435  1.7003
SD    0.0009  0.0045  0.0268  0.0919  0.0046  1.2632

일자|시간|구분  공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 B    0  2019-01-01  ...  0.403709  0.006300 -0.112221
1     2019-01-01 02 B    0  2019-01-01  ...  0.256784  0.005954 -0.132061
2     2019-01-01 03 B    0  2019-01-01  ...  0.169576  0.005526 -0.072633
3     2019-01-01 04 B    0  2019-01-01  ...  0.115783  0.005066  0.043694
4     2019-01-01 05 B    0  2019-01-01  ...  0.073214  0.004867  0.176287
...               ...  ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 B    0  2019-03-31  ...  0.462267 -0.000626  0.083326
2156  2019-03-31 21 B    0  2019-03-31  ...  0.627406  0.000832  0.002292
2157  2019-03-31 22 B    0  2019-03-31  ...  0.703771  0.001394 -0.001489
2158  2019-03-31 23 B    0  2019-03-31  ...  0.731248  0.001449 -0.047655
2159  2019-03-31 24 B    0  2019-03-31  ...  0.592089  0.001449 -0.046291

[2160 rows x 15 columns]

In [31]:
setup_c = setup(data=data_features_c, target='공급량_r', use_gpu=True, silent=True)
model_best = create_model('lightgbm')
prediction = predict_model(model_best, data=sub_c)
sub_c['공급량_r'] = prediction.Label
sub_c

MAE     MSE    RMSE      R2   RMSLE     MAPE
0     0.0490  0.0205  0.1432 -3.7249  0.0902  29.4153
1     0.0685  1.5469  1.2437 -0.0118  0.1189  13.3255
2     0.0543  0.0359  0.1896 -1.1438  0.1044  27.4498
3     0.0874  3.2048  1.7902 -0.0104  0.1385   8.3415
4     0.0718  1.5932  1.2622 -0.0575  0.1267  43.4094
5     0.0652  0.1507  0.3882 -0.5932  0.1309  20.1985
6     0.0595  0.0508  0.2254 -9.8214  0.1183  23.9699
7     0.0581  0.0583  0.2414 -2.1862  0.1110  42.2058
8     0.0546  0.0291  0.1707 -5.4050  0.1071  77.0968
9     0.0556  0.0328  0.1810 -6.4560  0.1080  13.0182
Mean  0.0624  0.6723  0.5836 -2.9410  0.1154  29.8431
SD    0.0107  1.0351  0.5760  3.1808  0.0135  19.2911

일자|시간|구분  공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 C    0  2019-01-01  ...  0.403709  0.006300  0.157468
1     2019-01-01 02 C    0  2019-01-01  ...  0.256784  0.005954  0.157468
2     2019-01-01 03 C    0  2019-01-01  ...  0.169576  0.005526  0.157468
3     2019-01-01 04 C    0  2019-01-01  ...  0.115783  0.005066  0.192163
4     2019-01-01 05 C    0  2019-01-01  ...  0.073214  0.004867  0.300562
...               ...  ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 C    0  2019-03-31  ...  0.462267 -0.000626  0.007526
2156  2019-03-31 21 C    0  2019-03-31  ...  0.627406  0.000832  0.013501
2157  2019-03-31 22 C    0  2019-03-31  ...  0.703771  0.001394 -0.066302
2158  2019-03-31 23 C    0  2019-03-31  ...  0.731248  0.001449 -0.086656
2159  2019-03-31 24 C    0  2019-03-31  ...  0.592089  0.001449 -0.087930

[2160 rows x 15 columns]

In [32]:
setup_d = setup(data=data_features_d, target='공급량_r', use_gpu=True, silent=True)
model_best = create_model('lightgbm')
prediction = predict_model(model_best, data=sub_d)
sub_d['공급량_r'] = prediction.Label
sub_d

MAE     MSE    RMSE      R2   RMSLE    MAPE
0     0.0341  0.0026  0.0511  0.9192  0.0393  1.4553
1     0.0330  0.0023  0.0485  0.9213  0.0378  0.9889
2     0.0340  0.0028  0.0525  0.9127  0.0404  1.2491
3     0.0339  0.0026  0.0508  0.9139  0.0393  1.0978
4     0.0338  0.0025  0.0498  0.9181  0.0385  1.3704
5     0.0326  0.0023  0.0481  0.9203  0.0381  1.0660
6     0.0336  0.0024  0.0486  0.9189  0.0381  1.9825
7     0.0334  0.0026  0.0508  0.9162  0.0395  1.2138
8     0.0335  0.0025  0.0496  0.9193  0.0379  1.4178
9     0.0348  0.0027  0.0522  0.9107  0.0409  1.0883
Mean  0.0337  0.0025  0.0502  0.9171  0.0390  1.2930
SD    0.0006  0.0001  0.0015  0.0034  0.0010  0.2749

일자|시간|구분  공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 D    0  2019-01-01  ...  0.403709  0.006300 -0.104801
1     2019-01-01 02 D    0  2019-01-01  ...  0.256784  0.005954 -0.126150
2     2019-01-01 03 D    0  2019-01-01  ...  0.169576  0.005526 -0.080825
3     2019-01-01 04 D    0  2019-01-01  ...  0.115783  0.005066  0.122151
4     2019-01-01 05 D    0  2019-01-01  ...  0.073214  0.004867  0.108023
...               ...  ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 D    0  2019-03-31  ...  0.462267 -0.000626  0.072333
2156  2019-03-31 21 D    0  2019-03-31  ...  0.627406  0.000832 -0.010573
2157  2019-03-31 22 D    0  2019-03-31  ...  0.703771  0.001394 -0.034929
2158  2019-03-31 23 D    0  2019-03-31  ...  0.731248  0.001449 -0.065597
2159  2019-03-31 24 D    0  2019-03-31  ...  0.592089  0.001449 -0.070329

[2160 rows x 15 columns]

In [33]:
setup_e = setup(data=data_features_e, target='공급량_r', use_gpu=True, silent=True)
model_best = create_model('lightgbm')
prediction = predict_model(model_best, data=sub_e)
sub_e['공급량_r'] = prediction.Label
sub_e

MAE     MSE    RMSE      R2   RMSLE    MAPE
0     0.0275  0.0017  0.0418  0.9312  0.0326  1.6683
1     0.0271  0.0016  0.0401  0.9337  0.0316  1.8294
2     0.0275  0.0018  0.0423  0.9300  0.0327  1.2016
3     0.0272  0.0018  0.0424  0.9292  0.0329  1.0342
4     0.0277  0.0017  0.0416  0.9311  0.0325  1.2343
5     0.0277  0.0019  0.0432  0.9290  0.0332  1.3960
6     0.0283  0.0019  0.0432  0.9316  0.0335  1.3889
7     0.0279  0.0018  0.0422  0.9304  0.0332  3.0005
8     0.0269  0.0017  0.0414  0.9346  0.0318  1.2465
9     0.0277  0.0017  0.0418  0.9359  0.0320  1.8215
Mean  0.0276  0.0018  0.0420  0.9317  0.0326  1.5821
SD    0.0004  0.0001  0.0009  0.0022  0.0006  0.5374

일자|시간|구분  공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 E    0  2019-01-01  ...  0.403709  0.006300 -0.114078
1     2019-01-01 02 E    0  2019-01-01  ...  0.256784  0.005954 -0.136685
2     2019-01-01 03 E    0  2019-01-01  ...  0.169576  0.005526 -0.084401
3     2019-01-01 04 E    0  2019-01-01  ...  0.115783  0.005066  0.045422
4     2019-01-01 05 E    0  2019-01-01  ...  0.073214  0.004867  0.148856
...               ...  ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 E    0  2019-03-31  ...  0.462267 -0.000626  0.078187
2156  2019-03-31 21 E    0  2019-03-31  ...  0.627406  0.000832  0.006190
2157  2019-03-31 22 E    0  2019-03-31  ...  0.703771  0.001394 -0.012834
2158  2019-03-31 23 E    0  2019-03-31  ...  0.731248  0.001449 -0.043190
2159  2019-03-31 24 E    0  2019-03-31  ...  0.592089  0.001449 -0.050564

[2160 rows x 15 columns]

In [34]:
setup_f = setup(data=data_features_f, target='공급량_r', use_gpu=True, silent=True)
model_best = create_model('lightgbm')
prediction = predict_model(model_best, data=sub_f)
sub_f['공급량_r'] = prediction.Label
sub_f

MAE     MSE    RMSE      R2   RMSLE    MAPE
0     0.0177  0.0017  0.0418  0.8441  0.0268  1.1096
1     0.0175  0.0006  0.0250  0.9401  0.0210  1.2370
2     0.0176  0.0008  0.0277  0.9321  0.0221  1.1173
3     0.0171  0.0006  0.0241  0.9460  0.0205  1.1694
4     0.0180  0.0012  0.0342  0.8899  0.0237  1.0955
5     0.0180  0.0018  0.0429  0.8419  0.0287  1.6097
6     0.0172  0.0006  0.0253  0.9421  0.0214  2.0241
7     0.0178  0.0007  0.0258  0.9377  0.0217  1.8963
8     0.0176  0.0007  0.0269  0.9345  0.0221  1.6342
9     0.0171  0.0007  0.0256  0.9409  0.0214  1.2418
Mean  0.0176  0.0009  0.0299  0.9149  0.0229  1.4135
SD    0.0003  0.0005  0.0068  0.0390  0.0026  0.3309

일자|시간|구분  공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 G    0  2019-01-01  ...  0.403709  0.006300 -0.111128
1     2019-01-01 02 G    0  2019-01-01  ...  0.256784  0.005954 -0.114065
2     2019-01-01 03 G    0  2019-01-01  ...  0.169576  0.005526 -0.062920
3     2019-01-01 04 G    0  2019-01-01  ...  0.115783  0.005066  0.011542
4     2019-01-01 05 G    0  2019-01-01  ...  0.073214  0.004867  0.073586
...               ...  ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 G    0  2019-03-31  ...  0.462267 -0.000626  0.046128
2156  2019-03-31 21 G    0  2019-03-31  ...  0.627406  0.000832 -0.003204
2157  2019-03-31 22 G    0  2019-03-31  ...  0.703771  0.001394 -0.015260
2158  2019-03-31 23 G    0  2019-03-31  ...  0.731248  0.001449 -0.045982
2159  2019-03-31 24 G    0  2019-03-31  ...  0.592089  0.001449 -0.041781

[2160 rows x 15 columns]

In [35]:
setup_g = setup(data=data_features_g, target='공급량_r', use_gpu=True, silent=True)
model_best = create_model('lightgbm')
prediction = predict_model(model_best, data=sub_g)
sub_g['공급량_r'] = prediction.Label
sub_g

MAE     MSE    RMSE      R2   RMSLE    MAPE
0     0.0513  0.0072  0.0849  0.8606  0.0578  1.6298
1     0.0549  0.0100  0.1000  0.8100  0.0649  1.4057
2     0.0546  0.0161  0.1267  0.7419  0.0668  1.3184
3     0.0516  0.0069  0.0832  0.8579  0.0571  1.5642
4     0.0527  0.0074  0.0859  0.8551  0.0590  1.7753
5     0.0545  0.0186  0.1364  0.6260  0.0670  2.0754
6     0.0639  0.6124  0.7825  0.0669  0.0930  2.2350
7     0.0553  0.0104  0.1018  0.7987  0.0658  1.8188
8     0.0534  0.0082  0.0904  0.8502  0.0593  1.5655
9     0.0572  0.0171  0.1308  0.6944  0.0693  2.5869
Mean  0.0549  0.0714  0.1723  0.7162  0.0660  1.7975
SD    0.0034  0.1804  0.2043  0.2290  0.0099  0.3758

일자|시간|구분  공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 H    0  2019-01-01  ...  0.403709  0.006300 -0.109168
1     2019-01-01 02 H    0  2019-01-01  ...  0.256784  0.005954 -0.176634
2     2019-01-01 03 H    0  2019-01-01  ...  0.169576  0.005526 -0.127810
3     2019-01-01 04 H    0  2019-01-01  ...  0.115783  0.005066  0.090628
4     2019-01-01 05 H    0  2019-01-01  ...  0.073214  0.004867  0.138734
...               ...  ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 H    0  2019-03-31  ...  0.462267 -0.000626  0.114230
2156  2019-03-31 21 H    0  2019-03-31  ...  0.627406  0.000832  0.018294
2157  2019-03-31 22 H    0  2019-03-31  ...  0.703771  0.001394 -0.051501
2158  2019-03-31 23 H    0  2019-03-31  ...  0.731248  0.001449 -0.077177
2159  2019-03-31 24 H    0  2019-03-31  ...  0.592089  0.001449 -0.066491

[2160 rows x 15 columns]

In [36]:
answer = {2583.34 : [], 2290.154 : [], 237.911 : [], 1422.478 : [], 3534.26 : [], 3982.757 : [], 560.896 : []}
answer_list = [2583.34, 2290.154, 237.911, 1422.478, 3534.26, 3982.757, 560.896]

In [37]:
sub_a

일자|시간|구분  공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 A    0  2019-01-01  ...  0.000000  0.000000 -0.112546
1     2019-01-01 02 A    0  2019-01-01  ...  0.000000  0.000000 -0.142575
2     2019-01-01 03 A    0  2019-01-01  ...  0.000000  0.000000 -0.103991
3     2019-01-01 04 A    0  2019-01-01  ...  0.000000  0.000000  0.016013
4     2019-01-01 05 A    0  2019-01-01  ...  0.000000  0.000000  0.124702
...               ...  ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 A    0  2019-03-31  ...  0.462267 -0.000626  0.047013
2156  2019-03-31 21 A    0  2019-03-31  ...  0.627406  0.000832 -0.009759
2157  2019-03-31 22 A    0  2019-03-31  ...  0.703771  0.001394 -0.029736
2158  2019-03-31 23 A    0  2019-03-31  ...  0.731248  0.001449 -0.042871
2159  2019-03-31 24 A    0  2019-03-31  ...  0.592089  0.001449 -0.051614

[2160 rows x 15 columns]

In [38]:
a_list = [2583.34]
for i in sub_a['공급량_r']:
    a_list.append((i+1)*a_list[-1])
a_list.pop(0)
sub_a['공급량'] = a_list
sub_a

일자|시간|구분            공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 A    2292.594755  2019-01-01  ...  0.000000  0.000000 -0.112546
1     2019-01-01 02 A    1965.728126  2019-01-01  ...  0.000000  0.000000 -0.142575
2     2019-01-01 03 A    1761.309684  2019-01-01  ...  0.000000  0.000000 -0.103991
3     2019-01-01 04 A    1789.514134  2019-01-01  ...  0.000000  0.000000  0.016013
4     2019-01-01 05 A    2012.670740  2019-01-01  ...  0.000000  0.000000  0.124702
...               ...            ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 A  202303.800988  2019-03-31  ...  0.462267 -0.000626  0.047013
2156  2019-03-31 21 A  200329.576632  2019-03-31  ...  0.627406  0.000832 -0.009759
2157  2019-03-31 22 A  194372.611856  2019-03-31  ...  0.703771  0.001394 -0.029736
2158  2019-03-31 23 A  186039.726618  2019-03-31  ...  0.731248  0.001449 -0.042871
2159  2019-03-31 24 A  176437.528166  2019-03-31  ...  0.592089  0.001449 -0.051614

[2160 rows x 15 columns]

In [39]:
a_list = [2290.154]
for i in sub_b['공급량_r']:
    a_list.append((i+1)*a_list[-1])
a_list.pop(0)
sub_b['공급량'] = a_list


In [49]:
sub_b.iloc[250:260, :]

일자|시간|구분          공급량          일자  ...      습도_r      기압_r     공급량_r
250  2019-01-11 11 B  5877.515427  2019-01-11  ... -0.207845  0.000773 -0.061414
251  2019-01-11 12 B  5374.982947  2019-01-11  ... -0.278446  0.000394 -0.085501
252  2019-01-11 13 B  4910.508120  2019-01-11  ... -0.324690 -0.000337 -0.086414
253  2019-01-11 14 B  4674.510466  2019-01-11  ... -0.349681 -0.001041 -0.048060
254  2019-01-11 15 B  4339.928500  2019-01-11  ... -0.353508 -0.001571 -0.071576
255  2019-01-11 16 B  4286.859151  2019-01-11  ... -0.294959 -0.001771 -0.012228
256  2019-01-11 17 B  4461.471705  2019-01-11  ... -0.180175 -0.001771  0.040732
257  2019-01-11 18 B  5019.507823  2019-01-11  ... -0.018684 -0.001733  0.125079
258  2019-01-11 19 B  5658.376295  2019-01-11  ...  0.120339 -0.001093  0.127277
259  2019-01-11 20 B  6041.223648  2019-01-11  ...  0.246042 -0.000181  0.067660

[10 rows x 15 columns]

In [41]:

a_list = [237.911]
for i in sub_c['공급량_r']:
    a_list.append((i+1)*a_list[-1])
a_list.pop(0)
sub_c['공급량'] = a_list
sub_c

일자|시간|구분           공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 C  2.753743e+02  2019-01-01  ...  0.403709  0.006300  0.157468
1     2019-01-01 02 C  3.187368e+02  2019-01-01  ...  0.256784  0.005954  0.157468
2     2019-01-01 03 C  3.689275e+02  2019-01-01  ...  0.169576  0.005526  0.157468
3     2019-01-01 04 C  4.398216e+02  2019-01-01  ...  0.115783  0.005066  0.192163
4     2019-01-01 05 C  5.720154e+02  2019-01-01  ...  0.073214  0.004867  0.300562
...               ...           ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 C  9.553095e+15  2019-03-31  ...  0.462267 -0.000626  0.007526
2156  2019-03-31 21 C  9.682071e+15  2019-03-31  ...  0.627406  0.000832  0.013501
2157  2019-03-31 22 C  9.040128e+15  2019-03-31  ...  0.703771  0.001394 -0.066302
2158  2019-03-31 23 C  8.256747e+15  2019-03-31  ...  0.731248  0.001449 -0.086656
2159  2019-03-31 24 C  7.530732e+15  2019-03-31  ...  0.592089  0.001449 -0.087930

[2160 rows x 15 columns]

In [42]:


a_list = [1422.478]
for i in sub_d['공급량_r']:
    a_list.append((i+1)*a_list[-1])
a_list.pop(0)
sub_d['공급량'] = a_list
sub_d

일자|시간|구분            공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 D    1273.400591  2019-01-01  ...  0.403709  0.006300 -0.104801
1     2019-01-01 02 D    1112.761591  2019-01-01  ...  0.256784  0.005954 -0.126150
2     2019-01-01 03 D    1022.822714  2019-01-01  ...  0.169576  0.005526 -0.080825
3     2019-01-01 04 D    1147.761764  2019-01-01  ...  0.115783  0.005066  0.122151
4     2019-01-01 05 D    1271.746795  2019-01-01  ...  0.073214  0.004867  0.108023
...               ...            ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 D  410440.969996  2019-03-31  ...  0.462267 -0.000626  0.072333
2156  2019-03-31 21 D  406101.256258  2019-03-31  ...  0.627406  0.000832 -0.010573
2157  2019-03-31 22 D  391916.705123  2019-03-31  ...  0.703771  0.001394 -0.034929
2158  2019-03-31 23 D  366207.957914  2019-03-31  ...  0.731248  0.001449 -0.065597
2159  2019-03-31 24 D  340452.760126  2019-03-31  ...  0.592089  0.001449 -0.070329

[2160 rows x 15 columns]

In [43]:

a_list = [3534.26]
for i in sub_e['공급량_r']:
    a_list.append((i+1)*a_list[-1])
a_list.pop(0)
sub_e['공급량'] = a_list
sub_e

일자|시간|구분           공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 E  3.131078e+03  2019-01-01  ...  0.403709  0.006300 -0.114078
1     2019-01-01 02 E  2.703106e+03  2019-01-01  ...  0.256784  0.005954 -0.136685
2     2019-01-01 03 E  2.474961e+03  2019-01-01  ...  0.169576  0.005526 -0.084401
3     2019-01-01 04 E  2.587378e+03  2019-01-01  ...  0.115783  0.005066  0.045422
4     2019-01-01 05 E  2.972526e+03  2019-01-01  ...  0.073214  0.004867  0.148856
...               ...           ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 E  1.812425e+06  2019-03-31  ...  0.462267 -0.000626  0.078187
2156  2019-03-31 21 E  1.823643e+06  2019-03-31  ...  0.627406  0.000832  0.006190
2157  2019-03-31 22 E  1.800239e+06  2019-03-31  ...  0.703771  0.001394 -0.012834
2158  2019-03-31 23 E  1.722487e+06  2019-03-31  ...  0.731248  0.001449 -0.043190
2159  2019-03-31 24 E  1.635391e+06  2019-03-31  ...  0.592089  0.001449 -0.050564

[2160 rows x 15 columns]

In [44]:

a_list = [3982.757]
for i in sub_f['공급량_r']:
    a_list.append((i+1)*a_list[-1])
a_list.pop(0)
sub_f['공급량'] = a_list
sub_f

일자|시간|구분           공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 G   3540.160722  2019-01-01  ...  0.403709  0.006300 -0.111128
1     2019-01-01 02 G   3136.352001  2019-01-01  ...  0.256784  0.005954 -0.114065
2     2019-01-01 03 G   2939.012896  2019-01-01  ...  0.169576  0.005526 -0.062920
3     2019-01-01 04 G   2972.936224  2019-01-01  ...  0.115783  0.005066  0.011542
4     2019-01-01 05 G   3191.702858  2019-01-01  ...  0.073214  0.004867  0.073586
...               ...           ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 G  63352.222496  2019-03-31  ...  0.462267 -0.000626  0.046128
2156  2019-03-31 21 G  63149.271400  2019-03-31  ...  0.627406  0.000832 -0.003204
2157  2019-03-31 22 G  62185.594020  2019-03-31  ...  0.703771  0.001394 -0.015260
2158  2019-03-31 23 G  59326.202388  2019-03-31  ...  0.731248  0.001449 -0.045982
2159  2019-03-31 24 G  56847.499452  2019-03-31  ...  0.592089  0.001449 -0.041781

[2160 rows x 15 columns]

In [45]:
a_list = [560.896]
for i in sub_g['공급량_r']:
    a_list.append((i+1)*a_list[-1])
a_list.pop(0)
sub_g['공급량'] = a_list
sub_g

일자|시간|구분          공급량          일자  ...      습도_r      기압_r     공급량_r
0     2019-01-01 01 H   499.663982  2019-01-01  ...  0.403709  0.006300 -0.109168
1     2019-01-01 02 H   411.406283  2019-01-01  ...  0.256784  0.005954 -0.176634
2     2019-01-01 03 H   358.824491  2019-01-01  ...  0.169576  0.005526 -0.127810
3     2019-01-01 04 H   391.344053  2019-01-01  ...  0.115783  0.005066  0.090628
4     2019-01-01 05 H   445.636967  2019-01-01  ...  0.073214  0.004867  0.138734
...               ...          ...         ...  ...       ...       ...       ...
2155  2019-03-31 20 H  1145.231487  2019-03-31  ...  0.462267 -0.000626  0.114230
2156  2019-03-31 21 H  1166.182343  2019-03-31  ...  0.627406  0.000832  0.018294
2157  2019-03-31 22 H  1106.122370  2019-03-31  ...  0.703771  0.001394 -0.051501
2158  2019-03-31 23 H  1020.755114  2019-03-31  ...  0.731248  0.001449 -0.077177
2159  2019-03-31 24 H   952.883862  2019-03-31  ...  0.592089  0.001449 -0.066491

[2160 rows x 15 columns]

In [ ]:
sub_concat = pd.DataFrame()
sub_concat = pd.concat([sub_concat, sub_a], axis=0)
sub_concat = pd.concat([sub_concat, sub_b], axis=0)
sub_concat = pd.concat([sub_concat, sub_c], axis=0)
sub_concat = pd.concat([sub_concat, sub_d], axis=0)
sub_concat = pd.concat([sub_concat, sub_e], axis=0)
sub_concat = pd.concat([sub_concat, sub_f], axis=0)
sub_concat = pd.concat([sub_concat, sub_g], axis=0)
sub_concat

In [58]:
sub_final = sub_concat[['일자|시간|구분', '공급량']]
sub_final

일자|시간|구분           공급량
0      2019-01-01 01 A  2.323613e+03
1      2019-01-01 02 A  2.086512e+03
2      2019-01-01 03 A  1.942292e+03
3      2019-01-01 04 A  1.992832e+03
4      2019-01-01 05 A  2.221312e+03
...                ...           ...
15115  2019-03-31 20 H  4.056900e+08
15116  2019-03-31 21 H  4.218230e+08
15117  2019-03-31 22 H  4.108610e+08
15118  2019-03-31 23 H  3.911308e+08
15119  2019-03-31 24 H  3.774011e+08

[15120 rows x 2 columns]

In [59]:
sub_final.to_csv('stationary.csv', encoding='utf-8', index=False)